<font color='red'><h1>Read this before running: <h1></font>


1. **paraphrase-multilingual-mpnet-base-v2** takes wayy too long to run but is supposed to produce high quality embeddings. Use with GPU will make it faster. Use that.
2. Change the percentage variable which will contain the amount of data that the model is being trained on.


## Importing and stuff

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install bertopic
!pip install datasets
!pip install hdbscan
!pip install sentence_transformers
!pip install umap-learn
!pip install transformers
!pip3 install sentence_transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 3.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 45.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.7/85.7 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 22.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 44.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.9/56.9 kB 7.2 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB

In [ ]:
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer

from bertopic import BERTopic
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer
from umap import UMAP
from hdbscan import HDBSCAN

from datasets import load_dataset

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from scipy.sparse import vstack, csr_matrix

from tqdm import tqdm

import re
import os


from gensim.utils import simple_preprocess
from gensim.corpora import Dictionary
from gensim.models.coherencemodel import CoherenceModel

from multiprocessing import Pool, cpu_count



/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [ ]:
dataset = load_dataset("csv",data_files="/content/drive/MyDrive/wiki.csv")
# dataset = dataset.shuffle()

Generating train split: 0 examples [00:00, ? examples/s]

## Describe the dataset

In [ ]:
dataset['train']

Dataset({
    features: ['id', 'text', 'title', 'url'],
    num_rows: 70377
})

## Take a subset of the articles (optional)

In [ ]:
# Access the 'train' split
dataset = dataset['train']

# Take the first 35,000 rows of the dataset
dataset = dataset.select(range(21000))

# Optionally shuffle the dataset
# first_half_dataset = first_half_dataset.shuffle()

print(f"Total rows in first half dataset: {len(dataset)}")

# Continue with the rest of your processing using first_half_dataset


Total rows in first half dataset: 21000


## Split the induvidual articles into sentences and remove numerical digits from them

In [ ]:
def sentence_tokenizer(text: str) -> list:

        terminator = ["।", "?", "!"]
        tokens = []
        for i in text:
            if i in terminator:
                my_string = text[:text.index(i)+1]
                text = text[text.index(i)+1:]
                tokens.append(my_string.strip())
        return tokens

def strip_numbers_from_text(text: str) -> str:
    # Regular expression to match words containing Bengali numerals anywhere in the text
    pattern = r'\b[^\s]*[০১২৩৪৫৬৭৮৯][^\s]*\b'

    # Remove all words that match the pattern
    text = re.sub(pattern, '', text)

    return text.strip()

def remove_english_words(text: str) -> str:
    # Regular expression to match words with English alphabets
    return re.sub(r'\b[a-zA-Z]+\b', '', text).strip()


In [ ]:
transformed_sentences = list(map(sentence_tokenizer, dataset['text']))
# transformed_sentences = list(map(sentence_tokenizer, train_test_split['test']['text']))

# flatten
flattened_sentences = [sentence for sublist in transformed_sentences for sentence in sublist]

# Apply the function to strip numbers from the beginning of each sentence
flattened_sentences = [strip_numbers_from_text(sentence) for sentence in flattened_sentences]


# Apply the function to remove English words from each sentence
flattened_sentences = [remove_english_words(sentence) for sentence in flattened_sentences]


len(flattened_sentences)

377941

In [ ]:
for sentence in flattened_sentences:
    if "আষক" in sentence:
        print(sentence)


তৃতীয়ধরনের ট্যাবলেটি আরও সস্তা এবং নেশায় আষক্তদের নিকট এটি ভেজাল বলে পরিচিত।


## Step 1/6 : Produce Induvidual Sentence Vectors from the sentences using SentenceTransformers

In [ ]:
# Initialize the embedding model
# embedding_model = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2")
# embedding_model = SentenceTransformer("paraphrase-multilingual-mpnet-base-v2")
embedding_model = SentenceTransformer("shihab17/bangla-sentence-transformer")
# embedding_model = SentenceTransformer("bengali-sentence-similarity-sbert")

# Define the path to save/load embeddings
embedding_path = "/content/drive/MyDrive/embeddings3.npy"


# Check if the embeddings already exist
if os.path.exists(embedding_path):
    print("Loading existing embeddings...")
    embeddings = np.load(embedding_path, allow_pickle=True)
else:
    print("Computing new embeddings...")
    stepCount = len(flattened_sentences) // 100
    print(f"Step Count: {stepCount}")
    embeddings = []

    for i, sentence in enumerate(tqdm(flattened_sentences, desc="Computing embeddings")):
        if len(embeddings) % stepCount == 0 and len(embeddings) > 0:
            np.save(embedding_path, embeddings)
            print(f"Saved {len(embeddings)} embeddings to {embedding_path}")

        embeddings.append(embedding_model.encode(sentence))

    # Convert the list of embeddings to a numpy array
    embeddings = np.array(embeddings)
    np.save(embedding_path, embeddings)

print(f"Total embeddings: {len(embeddings)}")

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/3.58k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/701 [00:00<?, ?B/s]

...

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Loading existing embeddings...
Total embeddings: 184063


In [ ]:
print(f"{embeddings.shape}")

(184063, 768)


## Step 2/6 : Reduce the embeddings down to a lower dimension

In [ ]:
# UMAP parameters
umap_params = {
    'n_neighbors': 30,
    'n_components': 5,
    'min_dist': 0.0,
    'metric': 'cosine',
    'low_memory': True
}

# Batch processing parameters
batch_size = 20000  # Adjust batch size based on memory constraints

# Initialize UMAP model
umap_model = UMAP(**umap_params)

# Placeholder for reduced embeddings
reduced_embeddings = []

# Process in batches with progress bar
for i in tqdm(range(0, len(embeddings), batch_size), desc="Processing Batches"):
    batch_embeddings = embeddings[i:i+batch_size]
    batch_reduced = umap_model.fit_transform(batch_embeddings)
    reduced_embeddings.append(batch_reduced)

# Concatenate batches into a single array
reduced_embeddings = np.concatenate(reduced_embeddings, axis=0)

Processing Batches: 100%|██████████| 10/10 [06:52<00:00, 41.28s/it]


In [ ]:
embedding_path = "/content/drive/MyDrive/reduced_embeddings3.npy"
np.save(embedding_path, reduced_embeddings)

In [ ]:
print(f"Reduced Embeddings: {reduced_embeddings.shape}")

Reduced Embeddings: (184063, 5)


## Step 3/6 : Group the embeddings into clusters

In [ ]:
hdbscan_model = HDBSCAN( metric='euclidean', cluster_selection_method='eom', prediction_data=True)
clusters = hdbscan_model.fit_predict(reduced_embeddings)

/usr/local/lib/python3.10/dist-packages/joblib/externals/loky/backend/fork_exec.py:38: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid = os.fork()


In [ ]:
print(f"Clusters shape: {clusters.shape}")

Clusters shape: (184063,)


In [ ]:
print(f"Cluster array: {clusters}")
print(f"All Cluster: {np.unique(clusters)}")

Cluster array: [3860 3816   -1 ...  521  521   -1]
All Cluster: [  -1    0    1 ... 3950 3951 3952]


## Step 4/6 : Get the term count vector for each sentence

In [ ]:
def collect_english_and_numerical_words(text: str) -> set:
    # Regular expression to match English and numerical words
    pattern = r'\b[A-Za-z0-9]+\b'
    return set(re.findall(pattern, text))

# Collect all English and numerical words from the articles
all_english_numerical_words = set()

# for article in train_test_split['test']['text']:
for article in dataset['text']:
    all_english_numerical_words.update(collect_english_and_numerical_words(article))

# Create a list of additional stopwords
additional_stopwords = list(all_english_numerical_words)

# Read from csv file
bengali_stopwords = pd.read_csv("/content/drive/MyDrive/stopwords_bangla - Sheet1.csv", header=None)[1].tolist()

combined_stopwords = additional_stopwords + bengali_stopwords

print(f"English Numerical Stopwords:{all_english_numerical_words}")
print(f"Bengali Stopwords: {bengali_stopwords} ")
print(f"Combined Stopwords: {combined_stopwords}")

English Numerical Stopwords:{'landscape', '946057', 'Sinitsa', 'weather', 'Pisma', 'Satara', 'needs', 'Rodenkirch', 'kumar', 'Lagomorpha', 'CXLII', 'hazardous', 'mmegi', 'hour', '1565', '7955', 'Mythology', 'Noreg', 'Dhakar', 'Suzanne', 'Harpercollins', 'Nakshi', 'Grawp', 'Screenwriters', '978', 'DashboardunionN', '790', 'Been', 'profound', 'Arun', '7686', 'gland', 'eighth', 'sentenced', 'Roberto', 'Gloucestershire', 'Andrea', 'malraux', 'monogentiobioside', 'protests', '3633300', 'MORI', '1cec', 'wanting', 'Sverker', 'unhcr', 'Floridi', 'Sivanath', 'Kerosene', 'embracing', 'kHz', 'Choroid', 'Vaisakha', 'Ancestor', 'inculcate', 'Mudslides', 'VOC', 'femaleness', 'Labeo', '5777', 'Loeb', 'Emblems', 'jn', '8B', 'Cup', 'Mohan', 'War', 'fonts', 'loses', 'Hence', 'Murthy', 'Grandison', 'Mei', '578', 'Promise', 'Babe', 'Albert', 'Supernovae', 'Khaleda', 'Damien', 'grandis', 'autonomous', 'sized', '1823', 'Antigens', 'asmetro', 'Ayne', 'pairs', 'Mahadaji', 'consumed', 'Unless', 'recovered', 'p

In [ ]:
def bangla_tokenizer(text):
    return text.split()

In [ ]:
vectorizer_model = CountVectorizer(stop_words=bengali_stopwords, min_df = 10, tokenizer = bangla_tokenizer)
document_term_matrix = vectorizer_model.fit_transform(flattened_sentences)

In [ ]:
print(f"Document Term Matrix: {document_term_matrix.shape}")

Document Term Matrix: (377941, 33454)


## Step 5/6 : C-TF-IDF Calculation for each class for all the classes

In [ ]:
from scipy.sparse import vstack, csr_matrix
import numpy as np

ctfidf_model = ClassTfidfTransformer()

# Define a function to aggregate documents by clusters
def aggregate_by_cluster(X, clusters):
    unique_clusters = np.unique(clusters)
    aggregated_matrix = []
    for cluster in unique_clusters:
        cluster_docs = X[clusters == cluster]
        aggregated_matrix.append(cluster_docs.sum(axis=0).A.flatten())  # Use .A to convert sparse matrix to array and flatten
    return np.array(aggregated_matrix)

# Ensure the document-term matrix is in sparse format
if not isinstance(document_term_matrix, csr_matrix):
    document_term_matrix = csr_matrix(document_term_matrix)

aggregated_matrix = aggregate_by_cluster(document_term_matrix, clusters)
print(f"Aggregated Matrix shape: {aggregated_matrix.shape}")

# Fit the transformer on the aggregated document-term matrix
ctfidf_model.fit(aggregated_matrix)

# Transform the document-term matrix into c-TF-IDF matrix based on clusters
ctfidf_matrix = ctfidf_model.transform(aggregated_matrix)

# Print shapes to verify
print(f"Aggregated Matrix shape: {aggregated_matrix.shape}")
print(f"c-TF-IDF Matrix shape: {ctfidf_matrix.shape}")

print(f"ClassTfIdf Matrix: {ctfidf_matrix.shape}")


Aggregated Matrix shape: (3954, 33454)


/usr/local/lib/python3.10/dist-packages/bertopic/vectorizers/_ctfidf.py:82: RuntimeWarning: divide by zero encountered in divide
  idf = np.log((avg_nr_samples / df)+1)


Aggregated Matrix shape: (3954, 33454)
c-TF-IDF Matrix shape: (3954, 33454)
ClassTfIdf Matrix: (3954, 33454)


In [ ]:
print(f"ClassTfIdf Matrix: {ctfidf_matrix.shape}")

ClassTfIdf Matrix: (3954, 33454)


## Step 6/6 : Extract topics and top words based on c-TF-IDF matrix

In [ ]:
# Step 6a: Define a function to extract top words for each topic
def extract_top_words(ctfidf_matrix, vectorizer_model, top_n_words=100):
    topics = {}
    feature_names = vectorizer_model.get_feature_names_out()  # Get feature names

    for i in range(ctfidf_matrix.shape[0]):
        # Get indices of top n words with highest c-TF-IDF scores
        top_indices = np.argsort(ctfidf_matrix[i])[::-1][:top_n_words]
        top_words = [feature_names[idx] for idx in top_indices]
        topics[f"Topic_{i}"] = top_words
    return topics

# Extract top words for each topic
topics = extract_top_words(ctfidf_matrix, vectorizer_model)

# Print or use the top words for each topic
for topic_id, top_words in topics.items():
    print(f"{topic_id}: {top_words}")


Topic_0: ['ক্যানিবাল', 'বার্গাস', 'তায়াম্মুম', 'বার্ণপুর', 'মহাবিদ্যা', 'ভল্ডেমর্টের', 'রস্\u200c', 'গাছুয়া', 'বালঘাট', 'মহাবিস্ফোরণ', 'মহাবোধি', 'ভিক্টোরিয়া’স', 'যৌনসুখ', 'কালাপানিয়া', 'হাট/বাজারগুলো', 'মীম', 'ইরোটিক', 'অহল্যা', 'মীজানুর', 'র\u200c্যাটল', 'অহল্যার', 'অ্যাকটিভিশন', 'দাপটে', 'সাহেরখালী', 'হাতশেপসুতের', 'অ্যান্টনির', 'গল্\u200cফের', 'লারস', 'প্রতিযোগীকেই', 'উইন্ডসরের', 'অলিন্দ', 'শূরা', 'বারুইপুর', 'লার্জ', 'পোস্টারে', 'জঙ্গলখাইন', 'রামসেসের', 'বারৈয়াঢালা', 'বোলতার', 'জগন্নাথকে', 'ব্যবহারকারিদের', 'জগদ্ধাত্রীর', 'ভিক্ষাং', 'ইস্কো', 'জগদ্ধাত্রি', 'কৃপাবলম্বনকরী', 'বারৈয়ারহাট', 'যৌনমিলনের', 'অ্যাডসেন্স', 'অ্যান্টিভাইরাস', 'সেগা', 'বাসিলিস্ক', 'স্বয়ংসেবক', 'রোম্যান্সের', 'পরিস্থিতিগত', 'ছনুয়া', 'আইসিসের', 'ছনহরা', 'সাহারবিল', 'গার্ডেন্স', 'রেওয়া', 'দস্তানার', 'ধূমাবতী', 'কালীপুর', 'সাইকি', 'ইনসুলিন', 'হাইলধর', 'সাইকি।', 'হাইরাম', 'সাইকিকে', 'দশমহাবিদ্যার', 'গিলাফ', 'মাইটভাঙ্গা', 'দানিকেন', 'মিশরিয়', 'দানিকেনের', 'কুসুমপুরা', 'পৌরসভা;', 'ছিপাতলী', 'অ্যামবিগ্রাম', '

## Calculate the Coherence Score for the model

In [ ]:
import gensim
from gensim.models.coherencemodel import CoherenceModel
from gensim.corpora import Dictionary

# Function to extract top words for each topic
def extract_top_words(ctfidf_matrix, vectorizer_model, top_n_words=10):
    topics = {}
    feature_names = vectorizer_model.get_feature_names_out()  # Get feature names

    for i in range(ctfidf_matrix.shape[0]):
        # Get indices of top n words with highest c-TF-IDF scores
        top_indices = np.argsort(ctfidf_matrix[i])[::-1][:top_n_words]
        top_words = [feature_names[idx] for idx in top_indices]
        topics[f"Topic_{i}"] = top_words
    return topics

# Extract top words for each topic
topics = extract_top_words(ctfidf_matrix, vectorizer_model)

# Function to calculate the coherence score using Gensim
def calculate_coherence_gensim(topics, texts):
    # Create a Gensim dictionary and corpus
    dictionary = Dictionary([text.split() for text in texts])
    corpus = [dictionary.doc2bow(text.split()) for text in texts]

    # Extract top words for each topic in the format required by Gensim
    top_words_list = [[word for word in topic_words if word in dictionary.token2id] for topic_words in topics.values()]

    # Create the CoherenceModel
    coherence_model = CoherenceModel(
        topics=top_words_list,
        texts=[text.split() for text in texts],
        dictionary=dictionary,
        coherence='c_v'
    )

    # Calculate the coherence score
    coherence_score = coherence_model.get_coherence()
    return coherence_score

# Calculate the coherence score for the extracted topics
average_coherence_score = calculate_coherence_gensim(topics, flattened_sentences)
print("Average Coherence Score:", average_coherence_score)


## Assign a topic for a new document

In [ ]:
new_document_1 = """মামলাটির নির্ণয়ের জন্য বিচারকেরা তাদের সঠিক ধারণা অনুযায়ী তথ্য বিশ্লেষণ করেন।
নির্ণয় দেওয়ার সময়ে বিচারকেরা সমস্যার প্রতিপক্ষের মতামতগুলি বিবেচনা করেন।
ন্যায়বিচারের প্রস্তুতির সময় বিচারকেরা বিভিন্ন আইনী সূত্র অনুসরণ করেন।"""

new_document_2 = """রবীন্দ্রনাথ ঠাকুরের কবিতা সাহিত্যিক বিশ্লেষণ করতে জনপ্রিয় হয়ে উঠেছে।
বাংলা সাহিত্যে কুমারদাসের রচনা প্রকৃতি ও ঐতিহ্যের উপর ভিত্তি করে লেখা হয়েছে।
বাংলা সাহিত্যে সংস্কৃতির মূল্যবান অংশ উল্লেখযোগ্যভাবে প্রতিষ্ঠিত রয়েছে।"""

new_document_3 = """নতুন প্রযুক্তি এসব বিদেশে প্রথমবারের মতো একটি ভার্সিটি স্বাধীনতার মধ্যে ব্যাপক উপযোগিতা পায়।
বাংলাদেশের প্রযুক্তি অগ্রগতিতে বিশেষভাবে জনপ্রিয় হয়েছে।
প্রযুক্তিগত অগ্রগতিতে অন্য দেশগুলির মতো বাংলাদেশ প্রযুক্তিগত প্রস্তুতি করতে সক্ষম হয়েছে।"""

new_document_4 = """সরকারি প্রযুক্তিতে সার্ভিস স্বাস্থ্যসেবা সরবরাহের জন্য প্রযুক্তি ব্যবহার করছে।
স্বাস্থ্য ও সমাজসেবার জন্য প্রযুক্তি উন্নয়নের দিকে অনেক প্রয়াস করা হয়েছে।
সামাজিক সেবার জন্য প্রযুক্তি প্রযুক্তির মাধ্যমে পরিস্থিতি উন্নত করা হয়েছে।"""

new_document_5 = """পূর্বাচারের সাংস্কৃতিক অধিকার এবং প্রয়োগের জন্য প্রয়োগিত হয়েছে।
ঐতিহাসিক মূল্যবান উপকরণের জন্য ব্যবহার করা হয়।
বিভিন্ন সাংস্কৃতিক উপকরণ ব্যবহার করা হয়েছে যার মাধ্যমে ঐতিহাসিক জীবনের তথ্য অনুসন্ধান করা হয়।"""

In [ ]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from collections import Counter

documents = [new_document_1, new_document_2, new_document_3, new_document_4, new_document_5]

# Example implementations of the preprocessing functions
def sentence_tokenizer(text: str) -> list:
    # Naive tokenizer based on '|' delimiter
    return text.split('|')

def strip_numbers_from_text(text: str) -> str:
    # Removes numbers from text
    return ''.join([char for char in text if not char.isdigit()])

def remove_english_words(text: str) -> str:
    # Removes English words from text
    return ' '.join([word for word in text.split() if not word.isascii()])

# Step 1: Preprocess the new document
def preprocess_new_document(text: str) -> list:
    # print(f"Original text: {text}")
    sentences = sentence_tokenizer(text)
    # print(f"Tokenized sentences: {sentences}")
    sentences = [strip_numbers_from_text(sentence) for sentence in sentences]
    # print(f"After stripping numbers: {sentences}")
    sentences = [remove_english_words(sentence) for sentence in sentences]
    # print(f"After removing English words: {sentences}")
    sentences = [sentence for sentence in sentences if sentence.strip()]  # Remove empty sentences
    # print(f"After removing empty sentences: {sentences}")
    return sentences

for new_document in documents:
  # Preprocess the new document
  preprocessed_sentences = preprocess_new_document(new_document)
  # print(f"Preprocessed Sentences: {preprocessed_sentences}")

  # Assuming you have embeddings of previously processed documents
  # Example: embeddings = np.random.rand(num_docs, embedding_dim)
  embeddings = np.random.rand(10, 768)  # Example embeddings for 10 documents

  # Step 2: Generate embeddings for the new document sentences (using your embedding_model)
  new_embeddings = np.array([embedding_model.encode(sentence) for sentence in preprocessed_sentences])

  # Check if embeddings are generated
  if new_embeddings.size == 0:
      print("No valid embeddings for the document.")
  else:
      # print(f"Embeddings: {new_embeddings.shape}")

      # Step 3: Calculate cosine similarity between new embeddings and existing document embeddings
      sim_matrix = cosine_similarity(new_embeddings, embeddings)
      # print(f"Similarity Matrix Shape: {sim_matrix.shape}")

      # Step 4: Predict topics based on the most similar document
      most_similar_doc_idx = np.argmax(np.max(sim_matrix, axis=0))  # Find the document with highest similarity
      assigned_topic = f"Topic_{most_similar_doc_idx}"

      print(f"Assigned Topic: {assigned_topic}")
